In [1]:
import numpy as np
import pandas as pd
import jieba
import json
import jieba.analyse
from tqdm import tqdm
import re
from collections import Counter
import math
import random
import numexpr as ne 
from operator import itemgetter
from gensim.models import KeyedVectors
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from gensim.models import Word2Vec
from sklearn.decomposition import TruncatedSVD
import warnings
warnings.filterwarnings('ignore')

In [2]:
data=pd.read_csv(r'F:\work\2021.1.4 query\latest_1m_essay.csv')
data=data.dropna(axis=0,how='any').reset_index(drop=True)
user_data=pd.read_csv(r'F:\work\2021.1.4 query\2w_search.csv')
user_data=user_data.dropna(axis=0,how='any').reset_index(drop=True)

In [3]:
#清洗query内容
def clean_data(data):
    data = data.replace('/', '，').replace('丨', '，').replace('！', '。').replace('？', '。').replace('：', '，').replace('~', '。').replace(',', '，').replace('-', '').replace(' ', '').lower()
    return data

In [4]:
tqdm.pandas(desc="my bar!")
data['title'] = data['c_title'].progress_apply(lambda x: clean_data(x))
user_data['query'] = user_data['search_words'].progress_apply(lambda x: clean_data(x))

my bar!: 100%|██████████| 4747862/4747862 [00:10<00:00, 435358.43it/s]


In [100]:
car_type=pd.read_csv(r'F:\work\2021.1.4 query\car_name.csv')
with open(r'C:\Users\JDD\工作文件\user_dict_query.txt', 'a',encoding="utf-8") as f:
    for i in car_type.index:
        goods_name=car_type['goods_name'][i]
        lower_goods_name=goods_name.lower()
        chinese = re.findall(".*?([\u4E00-\u9FA5]+).*?",lower_goods_name)
        eng=re.findall('[a-zA-Z0-9]+',lower_goods_name)
        for i in chinese:
            f.write(i)
            f.write('\n')
        name_lst=list(set(eng))
        for i in name_lst:
            if len(i)>2:
                f.write(i)
                f.write('\n')
        k=[x for x in name_lst if len(x)<=2]
        if len(k)>0:
            f.write(lower_goods_name)
            f.write('\n')

In [30]:
car_type=pd.read_csv(r'F:\work\2021.1.4 query\car_name.csv')
i=22
goods_name=car_type['goods_name'][i]
lower_goods_name=goods_name.lower()
chinese = re.findall(".*?([\u4E00-\u9FA5]+).*?",lower_goods_name)
eng=re.findall('[a-zA-Z0-9]+',lower_goods_name)
print(goods_name)
print(chinese)
print(eng)
print(eng+chinese)

升特8001
['升特']
['8001']
['8001', '升特']


In [101]:
#设置停用词
jieba.analyse.set_stop_words(r'C:\Users\JDD\工作文件\stopwords.txt')
f = open(r'C:\Users\JDD\工作文件\stopwords.txt','r',encoding='utf8')
stopwords = []  
for line in f:
    line = line.strip()
    stopwords.append(line)
#设置userdict
jieba.load_userdict(r'C:\Users\JDD\工作文件\user_dict_query.txt')
#设置idf path
jieba.analyse.set_idf_path(r'C:\Users\JDD\工作文件\idf.txt')
#设置stop_words
stop_words = set((
        "the", "of", "is", "and", "to", "in", "that", "we", "for", "an", "are",
        "by", "be", "as", "on", "with", "can", "if", "from", "which", "you", "it",
        "this", "then", "at", "have", "all", "not", "one", "has", "or", "that"
    ))
stop_content = open(r'C:\Users\JDD\工作文件\stopwords.txt', 'rb').read().decode('utf-8')
for line in stop_content.splitlines():
    stop_words.add(line)

In [7]:
valid_sentence_list = []
essay_tokens={}
total_freq=0
word_freq={}
for i in data.index:
    sentence=data['title'][i]
    sentence_cut = list(jieba.cut(sentence)) 
    sentence_temp = [j for j in sentence_cut if j not in stopwords]
    valid_sentence_list.append(sentence_temp)
    essay_tokens[i]=sentence_temp
    total_freq+=len(sentence_temp)
    for j in sentence_temp:
        word_freq.setdefault(j,0)
        word_freq[j]+=1
    print(i, sentence_temp)
print(len(valid_sentence_list))

0 ['机车', '柯受良', '重机枪', '面前', '秒', '成渣', '结局']
1 ['男孩子', '第一次', '机车', '体验']
2 ['ara', 'irx7x', '尾翼']
3 ['国内', '售价', '13.5', '万元', '宝马', '650gt', '摩托车', '购买']
4 ['紧随', 'mt09', '步伐', '202', 'yamaha', 'mt07', '外观', '运动', '排放', '欧', '标准']
5 ['摩旅', '人生', '赣州', '西藏', '一辈子', '短', '别忘了', '答应', '做', '事']
6 ['经验之谈', '铝合金', '牙盘']
7 ['特斯拉', '摩托车', 'model']
8 ['街上', '刷到', '无极', '500', 'ds', '实车', '一丝', '触动']
9 ['春风', '250s', '赛道', '测试']
10 ['摩旅', '日记', '惠水', '滴水岩']
11 ['变废为宝', '闪闪发亮', '本田', '发动机', '合金', '盖', '修复', '抛光', '全过程']
12 ['撩妹', '神器', '杜卡迪', 'supersport']
13 ['北欧', '女神', '832', 'cc', '六缸', '机车', '马力', '116.7', '匹']
14 ['摩旅', '中国', '120', '天', '摩友', '常用', '手势', '力量']
15 ['哈雷', '机车', '欣赏']
16 ['有钱人', '玩具', '杜卡迪', 'superleggera', 'v4', '香嘛']
17 ['雅马哈', 'cygnus', 'x125', '代', '劲战', '蹦', 'ttrs', '踏板']
18 ['昂贵', '情怀', '改款', '宝马', 'ninet', '202', '上市']
19 ['gymkhana', 'gp', '2019', 'stage1', 'haruhiko', 'tsujiie', 'gsx', 'r1000', 'uaichxo3oss', '1080']
20 ['爆改', '铃木', 'suzuki', 'gsx', 'r1000', '200

334 ['一分钟', '摩托车', '钻石', '车架']
335 ['哈雷', 'custom', '1250', '新车', '确认', '上市', '计划']
336 ['摩托', '界性', '价之王', '149cc', '爆发', '12', '马力', '高速', '90', '稳', '400']
337 ['收藏', '级', '摩托', '本田', '老金', '翼', '三轮', '出厂', '30', '年', '不服', '不行']
338 ['欢乐', '机车', '女骑士']
339 ['实用', '踏板车', '110', 'cc', '风冷', '输出', '马力', '开', '年', '难', '大修', '1.2', '万起']
340 ['女', '赛车手', '奥利维亚', '重伤', '中', '复活', '奥利维亚']
341 ['死侍', '影片', '中座', '驾', 'vespa', '150', '摩托车', '称', '踏板', '中', '劳斯莱斯']
342 ['暗黑', '版', 'vespa', '真的', '很酷']
343 ['车展', '10', '辆', '新款', '雅马哈', '踏板', '摩托']
344 ['摩旅', '日记', 'd62', '翻', '四座', '五千米', '达坂', '穿', '无人区', '由疆入', '藏']
345 ['摩旅', '•', '越来越', '喜欢', '远行']
346 ['全新', '宝马', 's1000rr', 'xr', '摩托车', '预售']
347 ['轩摩要', '记', '吸睛', '利器', '新晋', '网红', '春风', '250s']
348 ['宁哥', '推荐', '四款', '复古', 'cafe', '车型', '性价比', '超高', '尽显', '王者', '风范', 'ฅ', 'ฅ']
349 ['多维', '躺', '枪', '罗西', '摔车', '夸', '塔拉', '罗大', '优势', '夺冠']
350 ['铃木', 'uu', '125', '换灯', '分享']
351 ['carlos', 'moto', 'vlog', '37', '空腹', '勿', '车友', '聚会', 

674 ['motogp', '™', '201', '年', 'vr46', '学院', '车手', '观看', '荷兰', '站', 'moto', '比赛', 'mis', 'ano', '赛道', '日常', '训练', '结束']
675 ['摩托车', '链条', '拉长']
676 ['选', '头盔', '简述']
677 ['202', 'bmw', 's1000', '全新', '来袭']
678 ['毛病', '😂']
679 ['猛挚', 'cb190x', '开箱', '落户', '行驶', '200', '公里', '爱', '初体验']
680 ['姜戈', '打不着', '火']
681 ['腿', '避震', '凯越', '400x', '带伤', '长途', '西藏', '林芝']
682 ['ktm', '690', 'smcr', '改装', '天蝎', '排气', '声浪', '欣赏']
683 ['摩托车', '中', '长途旅行', '带上', '装备', '新手', '老手', '装备', '推荐']
684 ['kawasaki', 'z1000', '直线', '加速', '赛', '摩友', '太会', '玩']
685 ['宝马', '摩托', 'gs', '车系', '迈进', '四十周年']
686 ['意大利', '轻奢新', '品牌', '维特', '碳纤维', '头盔', '首度', '测评']
687 ['川崎', '国', 'x300', '未', '恢复', '两', '万公里', '川进', '青出', '感受']
688 ['2019', '8.28', '骑行', 'vlog', '车', '小姐姐', '车', '挡住', '头盔', '视角', '拍摄', '设备', 'pro', 'hero', '2018', '车型', 'gsx250r']
689 ['赛科龙', 'rt3', '大阳', '锐', '250', '选']
690 ['这辆', '摩旅', '越野', '宝马', 's1000', 'xr', '喜欢']
691 ['难', '超越', '摩托', '233', 'cc', '单缸', '风冷', '油耗', '低至', '3.3', '1.5', '万起值']


1000 ['选择', '动力', '温顺', 'cbr650', '选择', '阿普利亚', '660', '小钢炮']
1001 ['铃木', 'gsx', '250']
1002 ['省', '道', '风景', '挺不错']
1003 ['国产', '篇', '中国', '201', '年', '2019', '年', '最具', '创新', '杰出', '十大', '摩托车']
1004 ['万元', '座', '高', '780', '春风', '650nk', '街车']
1005 ['那场', '旅行']
1006 ['西班牙', '三个', '著名', '摩托车', '俱乐部']
1007 ['香港', '禁摩', '包容', '摩托车', '好处', '网友', '完', '秒', '懂']
1008 ['二行程', '行程']
1009 ['本田', 'rebel', '1100', '新', '专利', '曝光', '搭载', '非双', '同款', 'dct', '发动机']
1010 ['天马行空', '创意', '宝马', 'xe', 'smc', '电动', '边三轮', '帅炸']
1011 ['摩界', '盛事', '风雨', '陪伴', '摩友', '20', '年', 'moto', '致以', '崇高', '敬意']
1012 ['本田', 'cb', '300r']
1013 ['202', 'honda', 'cb', '650r', '巴西', '新色', '发表']
1014 ['小姐姐', 'indian', 'moto', 'rcy', 'cle', 'ftr1200', 'rally']
1015 ['宝马', '310r', '印度', '测评', '价格', '时']
1016 ['经济', '可靠', '都市', '牧羊人', '动态', '篇']
1017 ['202', '年', '第十九届', '中国', '摩博会', '全世界', '发出', '邀请', '推广']
1018 ['盘点', '摩托车', '开车', '广告']
1019 ['盘点', '热门', '千元级', '城市', '通勤', '踏板车', '操控', '灵活', '经济', '实惠']
1020 ['川崎', 'z400'

1335 ['车友问', '铃木', 'dl', '1050', '老婆', '西藏', '摩旅', '动力', '够用']
1336 ['出车', '实用', '小物', '推荐', '弹力', '膜']
1337 ['春风', '250s', '超', '心动', '改色']
1338 ['街车', '本田', '国', '电喷', '8.5', '千瓦', '11.5', '油箱', '离地', '161']
1339 ['头盔', '必成', '爆款', '摩雷士', 'r50']
1340 ['鲈鱼', '790', 'duke', '790', '第一次', '贴', '飞行']
1341 ['250nk', '摩旅', '进藏', '31', '林芝', '拉萨', '逮']
1342 ['新乡市', '增驾', '证', '流程']
1343 ['joe', 'roberts', '谈', 'moto2', 'motogp', '抉择']
1344 ['世界', 'django', 'ü', 'rkiye', '车友', 'onur', 'ö', 'zet', 'ç', '拍摄', '分享']
1345 ['小伙', '入手', '铃木', 'dl250', '拉力', '车', '嫌', '动力', '太猛', '太', '暴力', '直呼', '换车', '接受', '250', '大排量', '强', '动力', '车']
1346 ['幕后', '花絮', 'mir', 'motogp', '组', '首次', '登台']
1347 ['国产', '复古', '车新', '选择', '宗申', '赛科龙', 're3']
1348 ['春风', '跑车', '250s', '上市', '高配', '版', '216', '800', '元', '国产车', '首见', '滑动', '离合']
1349 ['nk', '250', '春风', '动力', '280', '飞鹰', 'r25', 'abs', '高配', '15', '800']
1350 ['正脸', '侧颜', '翘', '臀辣', '好看', '😜', '💅']
1351 ['新手', '公升', '车靠', '谱']
1352 ['雅马哈', '20', 'r1', '骑

...

88526 ['全新', '202', 'honda', 'cbr', '600rr', '详细', '解读']
88527 ['车主', '访谈', '说', '说', '不到', '低价', '车', '台荣', '探路者', '300', '值不值得', '买']
88528 ['天下', '骑谈', '•', '勇闯', 'mae', 'hong', 'son', '环线', '380', 'corner', '•', '摩界', '之旅']
88529 ['百公里', '3.67', '大阳', '锐', '250', '磨合期', '油耗']
88530 ['骑士', '低下头', '最帅', '集合', 'ga', 'meo', 'ver']
88531 ['2020款', '川崎', 'z900', '变得', '不像', '街车', '200', '骑行', '体验']
88532 ['证明', '骑上', '摩托车', '最靓', '仔', '系列']
88533 ['价值', '30', '摩托车', '起步', '输给', '玩具', '跑车', '太', '给面子']
88534 ['650', '匹', '极速', '425', '地表', '最强', '铃木', '涡轮', '隼', '出售']
88535 ['冬天', '封', '车骑', '心爱', '摩托', '上班']
88536 ['四年', '放弃', 'gsx', '700', '涡轮']
88537 ['贝纳利', 'trk', '金鹏', '502', '八百公里', '骑行', '感受']
88538 ['力帆', 'v16', '赛科龙', 'ra2', '更好']
88539 ['解说', '新型', 'ninja', 'zx', '25r', '机翻', '改进', '字幕']
88540 ['202', '杜卡迪', '怪兽', '谍照', '曝光', 'monster', 'monster']
88541 ['美国', '机车', '媒体', '评选', '12', '受欢迎', '高端', '摩托车', '全盔']
88542 ['旅行']
88543 ['岁', '钱江', '黄龙', '600', '街车', '国人', '看不上眼', '印度', 

89900 ['雅马哈', '中量级', '明星', '踏板', '油耗', '2.9', '续航', '400']
89901 ['日本', '妹子', '回老家', '摩旅', '记录']
89902 ['体验', '摩旅', '走', '组团', '走', '孟孟有', '话', '说']
89903 ['豪爵', 'nk150', '1000', '公里', '飞致', '250', '心得', '体会']
89904 ['无痕', '测车', '31', '期', '隆鑫', '无极', '300r', '测评']
89905 ['月', '摩旅', '2000', '公里', '花去', '120', '元', '保养费', '值不值']
89906 ['昔日', '大力神', '今日', '何安在']
89907 ['西安', '茯茶', '镇', '大峪', '一日游']
89908 ['单缸', '本田', 'xr', '400']
89909 ['1984', '雅马哈', 'xj6', '00', '改装']
89910 ['分享', '一组', 'mt09', '美照']
89911 ['光阳', '车型', '发布', '电动', '弯梁', 'adv', '踏板']
89912 ['竖', '大拇指', '雅马哈', '小钢炮', '单缸', '水冷', '15', '马力', '配', 'rcb', '氮气', '减震']
89913 ['想', '所见', '爱', '爱']
89914 ['一辆', '事故', '维修', '无极', '500r']
89915 ['贝纳利', '幼狮', 'leoncino', '800', '香不香']
89916 ['暴力', '国产', '最强', '街车', '贝纳利', '752', '骑行', '感受', '改装', '经验', '建议']
89917 ['摩旅', '云南', '休息', '老铁们', '野外', '洗澡', '洗衣', '做饭']
89918 ['济南', '矿', 'gong', '村', '一日', '骑', '再来', '地方']
89919 ['花式', '越野']
89920 ['性感', '小姐姐', '摆', '拍', '走红', '网络']
8992

90221 ['良心', '街车', '外观', '彰显', '档次', '184cc', '单缸', '风冷', '15', '马力', '1.6', '起步']
90222 ['飞致', '150', 'cbf', '150', 'df150', '适合', '送', '外卖']
90223 ['小伙', '骑', '川崎', 'z900', '第一次', '参加', '重庆', '摩博会', '现场', '阵势', '内心', '震撼']
90224 ['摩托车', '长途旅行', '跨', '骑车', '累', '踏板车', '累', '踏板车', '跨', '骑车']
90225 ['五羊本田', '猛鸷', 'cb190x', '车主', '一年', '800', '公里', '骑行', '感受', '分享', '省油', '续航', '远']
90226 ['无极', '300ds', '新手', '第一台', '探险', '摩托车', '两', '万出头']
90227 ['202', 'yamaha', 'mt', '125', '雅马哈', '小排量', '扭力', '大师']
90228 ['改装', '档案', '超大', '号', '咖啡杯', 'yamaha', 'xjr', '1300', 'cafe', 'racer']
90229 ['国外', '哈雷', '班歌', '大聚会', '每一款', '一件', '艺术品']
90230 ['说', '本田', '190', '天下第一', '小姐姐', '腿', '天下']
90231 ['dct', '本田', 'adv', '车主', '公认', '四大', '优点', '缺点']
90232 ['车友问', '龙嘉', '途', 'gv250', '哪款']
90233 ['巡弋', '180', '之旅', '巴郎山']
90234 ['重庆', '中', '梁山', '霸下意', '城堡', '掌上', '一日游']
90235 ['车主', '分享', '赛科龙', 'rt3', '环华', '摩旅', '行程', '超', '130', '天', '里程', '超', '2w', '公里']
90236 ['盘点', '老外', '评价', '201', '川崎', '6

90536 ['暴力', '选', '川崎', '泡妞', '选', '雅马哈', '颜值', '女生', '喜欢']
90537 ['rebel', '250', '摩旅', '装备', '强大', '辣', '眼睛', '日本', '改装', '分裂']
90538 ['国产', '摩托车', '推荐']
90539 ['狂暴', 'ktm', '尬', 'bmw', '信仰', '310gs', '390', 'adv', '入门级', '多功能', '车大', 'pk']
90540 ['快乐', '摩托车', '疯狂', '摇摆', '摇摆', '🤣', '🤣', '🤣']
90541 ['赣州', '周末', '摩旅', '活动', '说好', '走', '半路', '抛弃']
90542 ['水冷', '气门', '发动机', 'tcs', '循迹', '系统', 'ak', '光阳', 'krv', '新车', '详解']
90543 ['自由']
90544 ['摩托车', '加惯', '92', '号', '汽油', '加', '95', '号', '优缺点']
90545 ['五款', '省油', '摩托', '1000', '块', '跑', '一年', '风冷', '发动机', '雅马哈']
90546 ['妹子', '留座']
90547 ['摩托车', '骑得', '保养', '里程', '时间']
90548 ['bmw', 'r125', '0r', '媒體試', '駕會']
90549 ['复古', '机车', '彩绘', '定制']
90550 ['贝纳利', '金鹏', 'trk', '502', '国庆', '长假', '400', '公里', '往返', '骑行', '感受']
90551 ['川崎', 'zh2', '性能', '测试', '曝光', '极速', '289km', '堪比', '同级', '仿赛']
90552 ['摩旅', '神器', '2020款', '川崎', 'versys', 'x300', '实车', '展示', '感觉']
90553 ['跑', '川藏线', '重量级', '摩旅', '高颜值', '高', '配置', '一款', '一款', '昂贵']
90554 ['suzuki', 

90845 ['宝马', '发布', '新款', '拿铁', '复古', '系列', '车型']
90846 ['跨', '骑摩托车', '几档', '起步']
90847 ['专业']
90848 ['35', '年老', '车', '丝毫', '未见', '岁月', '痕迹', '1985', 'bmw', '100', '每日一车']
90849 ['宝妈', '美女', '甩头', '杀']
90850 ['山东', '滕州', '周末', '小跑', '记录']
90851 ['大排', '街车', '标榜', '配', '四缸', '水冷', '引擎', '高', '配置', '性能', '强悍']
90852 ['进军', '中量级', '跑车', '市场', 'ktmrc7', '双缸', '跑车', '渲染', '图', '曝光']
90853 ['宝马', '首度', '测试', '新款', 'bmw', '1000rr']
90854 ['想要', '壁纸', '评论', '区', '留言', '😏']
90855 ['万出头', '价格', '性价比', '高', '跨', '骑车']
90856 ['万元', '级', '城市', '踏板', 'led', '灯具', '液晶', '仪表', '配', '5.1', '升', '油箱', '噪音', '油耗', '低']
90857 ['体罚', '修行', '紫禁城', '骑', '火星', '基地']
90858 ['电影', '感', '滑胎', '开启', 'mv', '阿古斯塔', '380', '幸福生活']
90859 ['雅马哈', 'r1', '亮', '黑色', '实拍', '这漆面', '太亮', '镜子']
90860 ['摩旅', '西藏', '力帆', 'v16', '青藏线', '第二集']
90861 ['力帆', 'kpv', '150', '跨界', '踏板', '上市', '售价', '12980', '元']
90862 ['对不起', '赛车手', '真的', '骑', '弯梁', 'rossi', 'vi', 'ñ', 'ales', '东南亚', '场地', '比赛']
90863 ['玩车', '艺人', '王一博']
90864 ['皇家恩菲

In [8]:
#i=795
#sts=data['c_title'][i]
#cut_sts=valid_sentence_list[i]
#print(sts)
#print(cut_sts)

In [9]:
#存储语料库
corpus_arr = np.array(valid_sentence_list)
corpus_df = pd.DataFrame(data = corpus_arr, columns = ['sentence']) #元素为str list
#corpus_df.to_csv(r'F:\work\12.3 文章关键词\word2vec\corpus_df_20201225.csv',index=False)
#使用词袋形式储存样本，用lda进行聚类
corpus = list(corpus_df.sentence.values)
#word2vec training 
model =  Word2Vec(sentences = corpus, size = 50, min_count = 1, window = 3, compute_loss=True,
                  workers = 10, sg=1, sample=1e-4, hs = 0, negative = 30, iter = 20, sorted_vocab = 1)
model.save(r'F:\work\2021.1.4 query\model\model.model') #save model
model.wv.save_word2vec_format(r'F:\work\2021.1.4 query\vector\model.vector') #save vectors
print(len(model.wv.vocab))

51022


In [10]:
#model = Word2Vec.load(r'F:\work\2021.1.4 query\model\model.model')

In [11]:
#exp='银钢'
#print(exp,'---------------------------------------->')
#print(model.wv.similar_by_word(exp, topn =10))

In [12]:
#获取token的weight
def compute_word_index(data):
    a=0.001
    index=a/(a+word_freq[data]/total_freq)
    return index

#计算文章vector
def compute_essay_vector(data):
    vec=np.zeros([1,50],dtype=np.float32)
    for i in data:
        if i in model.wv.vocab.keys():
            vec+=model[i]*compute_word_index(i)
    scale=len(data)
    if scale>0:
        vec=vec/scale
    else:
        vec=vec
    return vec

#获取用户query分词结果
def cut_user_query(data):
    data_cut=list(jieba.cut(data))
    return data_cut

#去除common部分
def remove_first_principal_component(X):
    svd = TruncatedSVD(n_components=1, n_iter=7, random_state=0)
    svd.fit(X)
    pc = svd.components_
    XX = X - X.dot(pc.transpose()) * pc
    return XX

#向量单位化
def Unitization(a):
    len_a=np.linalg.norm(a)
    if len_a>0:
        a=a/len_a
    else:
        a=a
    return a

In [13]:
#计算文章vector
essay_vector={}
for i in essay_tokens.keys():
    essay_vector[i]=compute_essay_vector(essay_tokens[i])
    print(i)

#转为矩阵
item_lst=list(essay_vector.keys())
vecary= np.zeros((len(item_lst),50))
for i in item_lst:
    vecary[i]=Unitization(essay_vector[i])
vecary.shape

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

3498
3499
3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697


6774
6775
6776
6777
6778
6779
6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973


10042
10043
10044
10045
10046
10047
10048
10049
10050
10051
10052
10053
10054
10055
10056
10057
10058
10059
10060
10061
10062
10063
10064
10065
10066
10067
10068
10069
10070
10071
10072
10073
10074
10075
10076
10077
10078
10079
10080
10081
10082
10083
10084
10085
10086
10087
10088
10089
10090
10091
10092
10093
10094
10095
10096
10097
10098
10099
10100
10101
10102
10103
10104
10105
10106
10107
10108
10109
10110
10111
10112
10113
10114
10115
10116
10117
10118
10119
10120
10121
10122
10123
10124
10125
10126
10127
10128
10129
10130
10131
10132
10133
10134
10135
10136
10137
10138
10139
10140
10141
10142
10143
10144
10145
10146
10147
10148
10149
10150
10151
10152
10153
10154
10155
10156
10157
10158
10159
10160
10161
10162
10163
10164
10165
10166
10167
10168
10169
10170
10171
10172
10173
10174
10175
10176
10177
10178
10179
10180
10181
10182
10183
10184
10185
10186
10187
10188
10189
10190
10191
10192
10193
10194
10195
10196
10197
10198
10199
10200
10201
10202
10203
10204
10205
10206
10207
1020

12772
12773
12774
12775
12776
12777
12778
12779
12780
12781
12782
12783
12784
12785
12786
12787
12788
12789
12790
12791
12792
12793
12794
12795
12796
12797
12798
12799
12800
12801
12802
12803
12804
12805
12806
12807
12808
12809
12810
12811
12812
12813
12814
12815
12816
12817
12818
12819
12820
12821
12822
12823
12824
12825
12826
12827
12828
12829
12830
12831
12832
12833
12834
12835
12836
12837
12838
12839
12840
12841
12842
12843
12844
12845
12846
12847
12848
12849
12850
12851
12852
12853
12854
12855
12856
12857
12858
12859
12860
12861
12862
12863
12864
12865
12866
12867
12868
12869
12870
12871
12872
12873
12874
12875
12876
12877
12878
12879
12880
12881
12882
12883
12884
12885
12886
12887
12888
12889
12890
12891
12892
12893
12894
12895
12896
12897
12898
12899
12900
12901
12902
12903
12904
12905
12906
12907
12908
12909
12910
12911
12912
12913
12914
12915
12916
12917
12918
12919
12920
12921
12922
12923
12924
12925
12926
12927
12928
12929
12930
12931
12932
12933
12934
12935
12936
12937
1293

...

76236
76237
76238
76239
76240
76241
76242
76243
76244
76245
76246
76247
76248
76249
76250
76251
76252
76253
76254
76255
76256
76257
76258
76259
76260
76261
76262
76263
76264
76265
76266
76267
76268
76269
76270
76271
76272
76273
76274
76275
76276
76277
76278
76279
76280
76281
76282
76283
76284
76285
76286
76287
76288
76289
76290
76291
76292
76293
76294
76295
76296
76297
76298
76299
76300
76301
76302
76303
76304
76305
76306
76307
76308
76309
76310
76311
76312
76313
76314
76315
76316
76317
76318
76319
76320
76321
76322
76323
76324
76325
76326
76327
76328
76329
76330
76331
76332
76333
76334
76335
76336
76337
76338
76339
76340
76341
76342
76343
76344
76345
76346
76347
76348
76349
76350
76351
76352
76353
76354
76355
76356
76357
76358
76359
76360
76361
76362
76363
76364
76365
76366
76367
76368
76369
76370
76371
76372
76373
76374
76375
76376
76377
76378
76379
76380
76381
76382
76383
76384
76385
76386
76387
76388
76389
76390
76391
76392
76393
76394
76395
76396
76397
76398
76399
76400
76401
7640

81154
81155
81156
81157
81158
81159
81160
81161
81162
81163
81164
81165
81166
81167
81168
81169
81170
81171
81172
81173
81174
81175
81176
81177
81178
81179
81180
81181
81182
81183
81184
81185
81186
81187
81188
81189
81190
81191
81192
81193
81194
81195
81196
81197
81198
81199
81200
81201
81202
81203
81204
81205
81206
81207
81208
81209
81210
81211
81212
81213
81214
81215
81216
81217
81218
81219
81220
81221
81222
81223
81224
81225
81226
81227
81228
81229
81230
81231
81232
81233
81234
81235
81236
81237
81238
81239
81240
81241
81242
81243
81244
81245
81246
81247
81248
81249
81250
81251
81252
81253
81254
81255
81256
81257
81258
81259
81260
81261
81262
81263
81264
81265
81266
81267
81268
81269
81270
81271
81272
81273
81274
81275
81276
81277
81278
81279
81280
81281
81282
81283
81284
81285
81286
81287
81288
81289
81290
81291
81292
81293
81294
81295
81296
81297
81298
81299
81300
81301
81302
81303
81304
81305
81306
81307
81308
81309
81310
81311
81312
81313
81314
81315
81316
81317
81318
81319
8132

86071
86072
86073
86074
86075
86076
86077
86078
86079
86080
86081
86082
86083
86084
86085
86086
86087
86088
86089
86090
86091
86092
86093
86094
86095
86096
86097
86098
86099
86100
86101
86102
86103
86104
86105
86106
86107
86108
86109
86110
86111
86112
86113
86114
86115
86116
86117
86118
86119
86120
86121
86122
86123
86124
86125
86126
86127
86128
86129
86130
86131
86132
86133
86134
86135
86136
86137
86138
86139
86140
86141
86142
86143
86144
86145
86146
86147
86148
86149
86150
86151
86152
86153
86154
86155
86156
86157
86158
86159
86160
86161
86162
86163
86164
86165
86166
86167
86168
86169
86170
86171
86172
86173
86174
86175
86176
86177
86178
86179
86180
86181
86182
86183
86184
86185
86186
86187
86188
86189
86190
86191
86192
86193
86194
86195
86196
86197
86198
86199
86200
86201
86202
86203
86204
86205
86206
86207
86208
86209
86210
86211
86212
86213
86214
86215
86216
86217
86218
86219
86220
86221
86222
86223
86224
86225
86226
86227
86228
86229
86230
86231
86232
86233
86234
86235
86236
8623

90907
90908
90909
90910
90911
90912
90913
90914
90915
90916
90917
90918
90919
90920
90921
90922
90923
90924
90925
90926
90927
90928
90929
90930
90931
90932
90933
90934
90935
90936
90937
90938
90939
90940
90941
90942
90943
90944
90945
90946
90947
90948
90949
90950
90951
90952
90953
90954
90955
90956
90957
90958
90959
90960
90961
90962
90963
90964
90965
90966
90967
90968
90969
90970
90971
90972
90973
90974
90975
90976
90977
90978
90979
90980
90981
90982
90983
90984
90985
90986
90987
90988
90989
90990
90991
90992
90993
90994
90995
90996
90997
90998
90999
91000
91001
91002
91003
91004
91005
91006
91007
91008
91009
91010
91011
91012
91013
91014
91015
91016
91017
91018
91019
91020
91021
91022
91023
91024
91025
91026
91027
91028
91029
91030
91031
91032
91033
91034
91035
91036
91037
91038
91039
91040
91041
91042
91043
91044
91045
91046
91047
91048
91049
91050
91051
91052
91053
91054
91055
91056
91057
91058
91059
91060
91061
91062
91063
91064
91065
91066
91067
91068
91069
91070
91071
91072
9107

(91213, 50)

In [14]:
%%time
user_data['query_cut'] = user_data['query'].progress_apply(lambda x: cut_user_query(x))
user_data['query_vector'] = user_data['query_cut'].progress_apply(lambda x:compute_essay_vector(x))

my bar!: 100%|██████████| 4747862/4747862 [02:05<00:00, 37732.04it/s]


Wall time: 4min 47s


In [104]:
i=100

In [125]:
query_vec=user_data['query_vector'][i]
query_vec=Unitization(query_vec)
query_words=user_data['search_words'][i]
query_cuts=user_data['query_cut'][i]
print(query_words,query_cuts)
print('------'*8)
sim_matrix=np.dot(query_vec,vecary.T) 
sorted_list=sorted(enumerate(list(sim_matrix[0])), key=itemgetter(1),reverse=True)
for j,sim in sorted_list[:10]:
    title=data['c_title'][j]
    print(title)
    print(valid_sentence_list[j])
    print(sim)
    print('------'*8)
i+=1

雅马哈 FORCE 155 ['雅马哈', 'force', '155']
------------------------------------------------
force155改装
['force', '155', '改装']
0.9960921005516915
------------------------------------------------
黑曼巴號 -雅马哈FORCE 155
['黑曼巴號', '雅马哈', 'force', '155']
0.9928249370707178
------------------------------------------------
雅马哈Force155踏板更适合国内？
['雅马哈', 'force', '155', '踏板', '适合', '国内']
0.9657311858838598
------------------------------------------------
台湾改装踏板FORCE 155
['台湾', '改装', '踏板', 'force', '155']
0.9574077639792058
------------------------------------------------
爆改踏板 雅马哈FORCE 155
['爆改', '踏板', '雅马哈', 'force', '155']
0.9538366205935295
------------------------------------------------
大改Force就是要這樣改！「銀佛」 - YAMAHA FORCE 155
['大改', 'force', '這樣', '改', '銀佛', 'yamaha', 'force', '155']
0.9404024594682275
------------------------------------------------
2021 雅马哈 Aerox 155 战斗小踏板
['202', '雅马哈', 'aerox', '155', '踏板']
0.925592057963286
------------------------------------------------
YAMAHA The new XSR155
['yam